# Preprocessing

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import os
import pandas as pd
import seaborn as sns
import time

import torch
from torch.utils.data import DataLoader
import torch.utils.data as data_utils


In [ ]:
import torch



# Device
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

# Path of the model (saved/to save)
modelFolder = './models/'

# When True, retrain the whole model
retrain = True

# Downsample the dataset
ds = True

# Size of the split
trainSize = 0.75
valSize = 0.05
testSize = 0.20

# Specify number of seconds for the window. Default: 16
window_size = 16

# Model hyper-parameters
batch_size = 4
learning_rate = 1e-3

# Seed for reproducibility
seed = 42

# Classes to drop in the dataset
classes_to_drop=[
    'stabf','stab']



In [ ]:
import numpy as np
import os
import pandas as pd
import random

from imblearn.under_sampling import RandomUnderSampler
from sklearn import preprocessing
from sklearn.metrics import f1_score
from torch.utils.data import Dataset

import torch
import torch.nn as nn



def setSeed(seed=seed):
    """
    Setting the seed for reproducibility
    """
    random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = True

setSeed()

def min_max_norm(self,col):
    self._data[col]=(self._data[col]-self._data[col].min())/(self._data[col].max()-self._data[col].min())


def std_scaler(self,col):
    self._data[col]=(self._data[col]-self._data[col].mean())/(self._data[col].std())


def f1(test_loader, model):
    f1 = 0
    with torch.no_grad():
        for i, (data, labels) in enumerate(test_loader):
            outputs = model(data)
            pred = outputs.data.max(1, keepdim=True)[1]
            f1 += f1_score(labels, pred, average='macro')
    avg_f1 = f1/len(test_loader)
    return (avg_f1)


class CustomDataset(Dataset):
    def __init__(self, file_path='/kaggle/working/new_dataset.csv', classes_to_drop=classes_to_drop, window_size=window_size, normalize=True, normalize_method='mean_std', auth=False, target=None):

        self._window_size=window_size
        self._data=pd.read_csv(file_path)

        # if auth==True:
        #     if target != 'J':
        #         self._data = self._data[self._data['stabf'].isin([target, 'J'])]
        #     else:
        #         self._data = self._data[self._data['stabf'].isin([target, 'I'])]

        #     self._data['stabf'] = self._data['stabf'].apply(lambda x: target if x == target else 'Z')
        #     self._data['stabf'] = self._data['stabf'].map({target: 1, 'Z': 0}).fillna(0).astype(int)


        # # Random Undersampling
        # X = self._data.drop('stabf', axis=1)
        # y = self._data['stabf']

        # # sampler = RandomUnderSampler(sampling_strategy='not minority', random_state=seed)
        # # X_resampled, y_resampled = sampler.fit_resample(X, y)

        # # X_resampled['Class'] = y_resampled
        # self._data = X

        # The data is sorted by Class A,B,C the indexes of the dataframe have restarted by ignore index
        self._data = self._data.sort_values(by=['stabf'], inplace=False,ignore_index = True)

        # class_uniq contains the letters of the drivers A,B and it loops across all of them
        for class_uniq in list(self._data['stabf'].unique()):
            # Find the total number of elements belonging to a class
            tot_number=sum(self._data['stabf']==class_uniq)
            # Number of elements to drop so that the class element is divisible by window size
            to_drop=tot_number%window_size
            # Returns the index of the first element of the class
            index_to_start_removing=self._data[self._data['stabf']==class_uniq].index[0]
            # Drop element from first element to the element required
            self._data.drop(self._data.index[index_to_start_removing:index_to_start_removing+to_drop],inplace=True)


        # Resetting index of dataframe after dropping values
        self._data = self._data.reset_index()
        self._data = self._data.drop(['index'], axis=1)

        index_starting_class=[] # This array contains the starting index of each class in the df
        for class_uniq in list(self._data['stabf'].unique()):
            # Appending the index of first element of each clas
            index_starting_class.append(self._data[self._data['stabf']==class_uniq].index[0])

        # Create the sequence of indexs of the windows
        sequences=[]
        for i in range(len(index_starting_class)):
            # Check if beginning of next class is there
            if i!=len(index_starting_class)-1:
                ranges=np.arange(index_starting_class[i], index_starting_class[i+1])
            else:
                ranges = np.arange(index_starting_class[i], len(self._data))
            for j in range(0,len(ranges),int(self._window_size/2)):
                if len(ranges[j:j+self._window_size])==16:
                    sequences.append(ranges[j:j+self._window_size])
        self._sequences=sequences


        # Take only the 'Class' which are the actual labels and store it in the labels of self
        self._labels=self._data['stabf']
        # Dropping columns which have constant measurements because they would return nan in std
        self._data.drop(classes_to_drop, inplace=True, axis=1)

        # Function to normalize the data either with min_max or mean_std
        if normalize and not auth:
            for col in self._data.columns:
                if normalize_method=='min_max':
                    min_max_norm(self,col)
                elif normalize_method=="mean_std":
                    std_scaler(self,col)

        # Create the array holding the windowed multidimensional arrays
        X=np.empty((len(sequences), self._window_size, len(self._data.columns)))
        y=[]

        for n_row, sequence in enumerate(sequences):
            X[n_row,:,:]=self._data.iloc[sequence]
            # The corresponding driver of the sequence is the driver at first sequence
            y.append(self._labels[sequence[0]])

        assert len(y)==len(X)
        # Assign the windowed dataset to the X of self
        self._X= X

        # Targets is a transformed version of y with drivers are encoded into 0 to 9
        targets = preprocessing.LabelEncoder().fit_transform(y)
        class_labels = encoder.classes_
        for code, label in enumerate(class_labels):
          print(f'Code: {code} -> Label: {label}')
        targets = torch.as_tensor(targets)  # Just converting it to a pytorch tensor
        self._y=targets # Assign it to y of self


    def __len__(self):
        return len(self._X)


    def __getitem__(self, index):
        return torch.FloatTensor(self._X[index,:,:]), self._y[index]


def evaluate(model, dataloader, criterion):
    model.eval()
    running_loss = 0.0
    running_corrects = 0
    y_true = []
    y_pred = []

    for inputs, labels in dataloader:
        inputs = inputs.to(device)
        labels = labels.to(device)

        inputs = inputs
        labels = labels

        # Forward pass
        with torch.no_grad():
            outputs = model(inputs)
            loss = criterion(outputs, labels)

        _, preds = torch.max(outputs, 1)
        running_loss += loss.item() * inputs.size(0)
        running_corrects += torch.sum(preds == labels.data)

        # Collect predictions and true labels
        y_true += labels.data.cpu().numpy().tolist()
        y_pred += preds.cpu().numpy().tolist()

    # Calculate accuracy and loss
    epoch_loss = running_loss / len(dataloader.dataset)
    epoch_acc = running_corrects.double() / len(dataloader.dataset)
    epoch_f1 = f1_score(y_true, y_pred, average='macro')

    return epoch_loss, epoch_acc, epoch_f1


def evaluateBinary(model, dataloader, criterion):
    model.eval()
    running_loss = 0.0
    running_corrects = 0
    y_true = []
    y_pred = []

    for inputs, labels in dataloader:
        inputs = inputs.to(device)
        labels = labels.to(device)

        # Forward pass
        with torch.no_grad():
            outputs = model(inputs)
            # loss = criterion(outputs, labels)
            loss = criterion(outputs.squeeze(), labels.float())

        _, preds = torch.max(outputs, 1)
        # preds = (outputs > 0.5).float()
        running_loss += loss.item() * inputs.size(0)
        running_corrects += torch.sum(preds == labels.data)

        # Collect predictions and true labels
        y_true += labels.data.cpu().numpy().tolist()
        y_pred += preds.cpu().numpy().tolist()

    # Calculate accuracy and loss
    epoch_loss = running_loss / len(dataloader.dataset)
    epoch_acc = running_corrects.double() / len(dataloader.dataset)
    epoch_f1 = f1_score(y_true, y_pred, average='macro')

    return epoch_loss, epoch_acc, epoch_f1



In [ ]:
dataset_path = '/kaggle/input/smart-gid-stability/smart_grid_stability_augmented.csv'
df = pd.read_csv(dataset_path)
df

In [ ]:
from sklearn.preprocessing import LabelEncoder

encoder = LabelEncoder()
df['stabf'] = encoder.fit_transform(df['stabf'])

# Retrieve the mapping of numerical codes to original class labels
class_labels = encoder.classes_

# Display the mapping
for code, label in enumerate(class_labels):
    print(f'Code: {code} -> Label: {label}')
df

In [ ]:
df.to_csv('new_dataset.csv', index=False)
df

In [ ]:
import torch
import numpy as np
np.random.seed(seed)
torch.manual_seed(seed)
torch.cuda.manual_seed(seed)
torch.cuda.manual_seed_all(seed)
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = True


In [ ]:
a = CustomDataset()

# Defining sizes
train_size = int(trainSize * len(a))
val_size = int(valSize * len(a))
test_size = len(a)-train_size-val_size

train_dataset, val_dataset, test_dataset = torch.utils.data.random_split(
    a, [train_size, val_size, test_size])


train_loader = torch.utils.data.DataLoader(dataset=train_dataset,
                                           batch_size=batch_size,
                                           shuffle=False,
                                           drop_last=True)

validation_loader = torch.utils.data.DataLoader(dataset=val_dataset,
                                                batch_size=batch_size,
                                                shuffle=False,
                                                drop_last=True)

test_loader = torch.utils.data.DataLoader(dataset=test_dataset,
                                          batch_size=batch_size,
                                          shuffle=False,
                                          drop_last=True)

# Bayesian LSTM stability prediction

In [ ]:
!pip install bayesian-torch

In [ ]:
from bayesian_torch.layers import LinearFlipout,LSTMFlipout
import torch.nn as nn
import torch.optim as optim


In [ ]:
pip install adversarial-robustness-toolbox


In [ ]:
import time
import torch.nn as nn
import torch.optim as optim

# Check if CUDA is available and set the device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

class BayesianRNN(nn.Module):
    def __init__(self, batch_size, window_size, num_features):
        super(BayesianRNN, self).__init__()
        self.lstm1 = LSTMFlipout(num_features, 110)
        self.lstm2 = LSTMFlipout(110, 220)
        self.fc = LinearFlipout(220, 1)  # Output a single value for binary classification
        self.sigmoid = nn.Sigmoid()  # Use sigmoid for binary classification

    def forward(self, x):
        lstm1_out, _, kl_lstm = self.lstm1(x)
        lstm2_out, _, kl_lstm1 = self.lstm2(lstm1_out)
        fc_out, kl_fc = self.fc(lstm2_out)
        out = self.sigmoid(fc_out[:, -1, :])  # Apply sigmoid activation function for binary classification
        return out, kl_lstm + kl_lstm1 + kl_fc

# Assuming train_loader is defined elsewhere
inputs, _ = next(iter(train_loader))
model5 = BayesianRNN(inputs.shape[0], inputs.shape[1], inputs.shape[2])
model5 = model5.to(device)

optimizer = optim.Adam(model5.parameters(), lr=0.001)  # Use Adam optimizer
criterion = nn.BCELoss()  # Binary cross-entropy loss

n_epochs = 20
start_time = time.time()

for epoch in range(n_epochs):
    model5.train()  # Set model to train mode

    train_loss = 0.0
    train_corrects = 0

    for inputs, labels in train_loader:
        inputs, labels = inputs.to(device), labels.to(device)

        # Reshape labels to match the output shape [batch_size, 1]
        labels = labels.view(-1, 1).float()  # Convert labels to float for BCELoss

        optimizer.zero_grad()  # Zero the parameter gradients

        outputs, kl_divergence = model5(inputs)  # Forward pass

        # Calculate loss as BCELoss plus KL divergence
        loss = criterion(outputs, labels) + 0.1 * kl_divergence
        loss.backward()
        optimizer.step()  # Update weights using the gradients

        # Update statistics
        train_loss += loss.item() * inputs.size(0)

        # Threshold the outputs at 0.5 to make predictions (binary classification)
        preds = (outputs > 0.5).float()  # Threshold outputs for binary predictions
        train_corrects += torch.sum(preds == labels).item()

    # Calculate epoch statistics
    train_loss = train_loss / len(train_loader.dataset)
    train_acc = float(train_corrects) / len(train_loader.dataset)

    print(f"Epoch {epoch+1}/{n_epochs} -- Train Loss: {train_loss:.4f} -- Train Accuracy: {train_acc:.4f}")

end_time = time.time()
training_time = end_time - start_time
print(f"Total Training Time: {training_time:.2f} seconds")
total_params = sum(p.numel() for p in model5.parameters())
print(f"Total Model Parameters: {total_params}")


In [ ]:
# Calculate accuracy
correct_predictions = 0
total_samples = 0

y_true = []
y_pred = []

for inputs, labels in test_loader:
    inputs, labels = inputs.to(device), labels.to(device)
    outputs,_ = model5(inputs)
    predictions = (outputs > 0.5).float()

    for p, l in zip(predictions, labels.float()):
        if p == l:
            correct_predictions += 1

    total_samples += labels.size(0)

    y_true.extend(labels.cpu().numpy())
    y_pred.extend(predictions.cpu().numpy())

acc = correct_predictions/total_samples
f1 = f1_score(y_true, y_pred, average='binary')

print('[👑 TEST GRU AUTH]\n')
print(f'[🎯 ACCURACY] {acc:.3f}')
print(f'[⚖️ F1 SCORE] {f1:.3f}')

# GAN-GRID against Beysain-LSTM

In [ ]:
class Generator(nn.Module):
    def __init__(self, batch_size, window_size, num_features,):
        super(Generator, self).__init__()
        self.batch_size = batch_size
        self.num_features = num_features
        self.window_size = window_size
        self.layer1 = nn.Linear(num_features, 128)
        self.layer2 = nn.Linear(128, 256)
        self.layer3 = nn.Linear(256, 512)
        self.layer4 = nn.Linear(512, batch_size*window_size)
        self.layer5 = nn.Linear(batch_size*window_size, num_features)

        self.leaky_relu = nn.LeakyReLU(0.2)

    def forward(self, x):
        x = self.leaky_relu(self.layer1(x))
        x = self.leaky_relu(self.layer2(x))
        x = self.leaky_relu(self.layer3(x))
        x = self.leaky_relu(self.layer4(x))
        x = self.layer5(x)
        return x

In [ ]:
def train_gan(generator, surrogate, label, train_loader, num_epochs=100, lr=0.001, device=torch.device('cpu'), ml=False, num_episodes=150):

    losses = []

    if not ml:
        generator = generator.to(device)
        surrogate = surrogate.to(device)

        # for model in surrogate.models:
        #     model.to(device)
        #     model.train()

    # Define the loss function and optimizer
    binary_cross_entropy_loss = nn.BCEWithLogitsLoss()
    generator_optimizer = torch.optim.Adam(generator.parameters(), lr=lr)

    # Define the reinforcement learning parameters
    max_episode_length = 10
    alpha = 0.1
    gamma = 0.9

    for episode in range(num_episodes):
        # Initialize the latent input and the episode reward
        latent_input = torch.randn(4, 16, 12).to(device)
        episode_reward = 0

        for step in range(max_episode_length):
            # Generate a sample with the current latent input
            fake_input = generator(latent_input)

            # Evaluate the sample with the surrogate model
            if not ml:
                surrogate_output,_ = surrogate(fake_input)
            else:
                surrogate_output = []
                # Looping through each
                for group in fake_input:
                    # Flatten the group to make it
                    flat_group = group.view(-1, group.size(-1)).detach().numpy()
                    # Get the probabilities
                    probabilities,_ = surrogate.predict_proba(flat_group)
                    mean_probabilities = np.mean(probabilities, axis=0)
                    # Append the probabilities to the array
                    surrogate_output.append(mean_probabilities)
                with torch.no_grad():
                    surrogate_output = torch.tensor(surrogate_output, requires_grad=True)

            predictions = (surrogate_output > 0.5).float()
            targets = torch.randint_like(predictions, 0, 2)
            reward = (predictions == targets).float().mean().item()
            episode_reward += reward

            # Update the latent input using reinforcement learning
            td_error = reward - episode_reward
            latent_input += alpha * td_error * gamma**step * torch.randn_like(latent_input)

        # Update the generator using the final latent input of the episode
        generator_optimizer.zero_grad()
        fake_input = generator(latent_input)

        if not ml:
            surrogate_output,_ = surrogate(fake_input)
        else:
            surrogate_output = []
            # Looping through
            for group in fake_input:
                flat_group = group.view(-1, group.size(-1)).detach().numpy()
                # Get the probabilities
                probabilities._ = surrogate.predict_proba(flat_group)
                mean_probabilities = np.mean(probabilities, axis=0)
                # Append the probabilities to the array
                surrogate_output.append(mean_probabilities)
            with torch.no_grad():
                surrogate_output = torch.tensor(surrogate_output, requires_grad=True)

        target_labels = targets.view(-1, 1).float()
        target_labels = torch.full_like(target_labels, label)

        generator_loss = binary_cross_entropy_loss(surrogate_output, target_labels)

        if ml:
            generator_optimizer.zero_grad()

        generator_loss.backward()
        generator_optimizer.step()

        losses.append(generator_loss.item())

        if episode % 10 == 0:
            print(f'[⏭️ EP {episode}/{num_episodes} | D{label}] LOSS: {round(generator_loss.item(), 3)}')

    print()

    return generator, losses

In [ ]:
lr = 3e-3

generators = []
losses = []

inputs, classes = next(iter(train_loader))

# For each driver
for d in range(1):
        print(f'[🤖 GENERATORS] Label {d}')

        batch_size, window_size, num_features = inputs.shape
        generator = Generator(batch_size, window_size, num_features)
        surrogate_model = model5

        generator, loss = train_gan(generator, surrogate_model, train_loader=train_loader, num_epochs=20, lr=lr, label=0, ml=False, num_episodes=100)
        print()

        generators.append(generator)
        losses.append(loss)

Restart the process if the gennrator did not converge in the first try

In [ ]:
results = []

threshold = 0.5
device = torch.device("cuda")
model5.to(device)
for i in range(1):
    predicted_labels = []
    generator = generators[i].to(device)

    for batch in test_loader:
        input_batch, true_labels = batch[0].to(device), batch[1].to(device)
        # Generate data
        generated_data = generator(torch.randn(4, 16, 12).to(device))
        # generated_data = generated_data * ones_tensor

        # Add the result to the ones tensor
        final_result =  generated_data.to(device)

        # Get the surrogate outputs for each sample in the generated data
        surrogate_outputs ,_= model5(final_result)

        # Apply the threshold for binary classification
        predicted_labels_batch = (surrogate_outputs > threshold).float()

        # Append the predicted labels to the lists
        predicted_labels.extend(predicted_labels_batch.squeeze().tolist())  # Squeeze the tensor

    asr = predicted_labels.count(0) / len(predicted_labels)
    results.append(asr)
    print(f'[👑 DRIVER {i}] ASR: {round(asr, 3)}')

# # Uncertainty-Based Adversarial Detection
# Using Joint Entropy and Information Metric

In [ ]:
# Copyright (C) 2024 Intel Labs
#
# BSD-3-Clause License
#
# Redistribution and use in source and binary forms, with or without modification,
# are permitted provided that the following conditions are met:
# 1. Redistributions of source code must retain the above copyright notice,
#    this list of conditions and the following disclaimer.
# 2. Redistributions in binary form must reproduce the above copyright notice,
#    this list of conditions and the following disclaimer in the documentation
#    and/or other materials provided with the distribution.
# 3. Neither the name of the copyright holder nor the names of its contributors
#    may be used to endorse or promote products derived from this software
#    without specific prior written permission.
#
# THIS SOFTWARE IS PROVIDED BY THE COPYRIGHT HOLDERS AND CONTRIBUTORS "AS IS"
# AND ANY EXPRESS OR IMPLIED WARRANTIES, INCLUDING, BUT NOT LIMITED TO,
# THE IMPLIED WARRANTIES OF MERCHANTABILITY AND FITNESS FOR A PARTICULAR PURPOSE
# ARE DISCLAIMED.  IN NO EVENT SHALL THE COPYRIGHT HOLDER OR CONTRIBUTORS
# BE LIABLE FOR ANY DIRECT, INDIRECT, INCIDENTAL, SPECIAL, EXEMPLARY,
# OR CONSEQUENTIAL DAMAGES (INCLUDING, BUT NOT LIMITED TO, PROCUREMENT
# OF SUBSTITUTE GOODS OR SERVICES; LOSS OF USE, DATA, OR PROFITS;
# OR BUSINESS INTERRUPTION) HOWEVER CAUSED AND ON ANY THEORY OF LIABILITY,
# WHETHER IN CONTRACT, STRICT LIABILITY, OR TORT (INCLUDING NEGLIGENCE
# OR OTHERWISE) ARISING IN ANY WAY OUT OF THE USE OF THIS SOFTWARE,
# EVEN IF ADVISED OF THE POSSIBILITY OF SUCH DAMAGE.
#
# Utily functions for variational inference in Bayesian deep neural networks
#
# @authors: Ranganath Krishnan
#
# ===============================================================================================

def entropy(prob):
    return -1 * np.sum(prob * np.log(prob + 1e-15), axis=-1)


def predictive_entropy(mc_preds):
    """
    Compute the entropy of the mean of the predictive distribution
    obtained from Monte Carlo sampling during prediction phase.
    """
    return entropy(np.mean(mc_preds, axis=0))


def mutual_information(mc_preds):
    """
    Compute the difference between the entropy of the mean of the
    predictive distribution and the mean of the entropy.
    """
    mc_preds = np.array(mc_preds)  
    mutual_info = entropy(np.mean(mc_preds, axis=0)) - np.mean(entropy(mc_preds),
                                                               axis=0)
    return mutual_info


def get_rho(sigma, delta):
    """
    sigma is represented by softplus function  'sigma = log(1 + exp(rho))' to make sure it
    remains always positive and non-transformed 'rho' gets updated during backprop.
    """
    rho = torch.log(torch.expm1(delta * torch.abs(sigma)) + 1e-20)
    return rho


def MOPED(model, det_model, det_checkpoint, delta):
    """
    Set the priors and initialize surrogate posteriors of Bayesian NN with Empirical Bayes
    MOPED (Model Priors with Empirical Bayes using Deterministic DNN)

    Example implementation for Bayesian model with variational layers.

    Reference:
    [1] Ranganath Krishnan, Mahesh Subedar, Omesh Tickoo. Specifying Weight Priors in
        Bayesian Deep Neural Networks with Empirical Bayes. Proceedings of the AAAI
        Conference on Artificial Intelligence. AAAI 2020.
        https://arxiv.org/abs/1906.05323
    """
    det_model.load_state_dict(torch.load(det_checkpoint))
    for (idx, layer), (det_idx,
                       det_layer) in zip(enumerate(model.modules()),
                                         enumerate(det_model.modules())):
        if (str(layer) == 'Conv1dReparameterization()'
                or str(layer) == 'Conv2dReparameterization()'
                or str(layer) == 'Conv3dReparameterization()'
                or str(layer) == 'ConvTranspose1dReparameterization()'
                or str(layer) == 'ConvTranspose2dReparameterization()'
                or str(layer) == 'ConvTranspose3dReparameterization()'
                or str(layer) == 'Conv1dFlipout()'
                or str(layer) == 'Conv2dFlipout()'
                or str(layer) == 'Conv3dFlipout()'
                or str(layer) == 'ConvTranspose1dFlipout()'
                or str(layer) == 'ConvTranspose2dFlipout()'
                or str(layer) == 'ConvTranspose3dFlipout()'):
            #set the priors
            layer.prior_weight_mu = det_layer.weight.data
            if layer.prior_bias_mu is not None:
               layer.prior_bias_mu = det_layer.bias.data

            #initialize surrogate posteriors
            layer.mu_kernel.data = det_layer.weight.data
            layer.rho_kernel.data = get_rho(det_layer.weight.data, delta)
            if layer.mu_bias is not None:
               layer.mu_bias.data = det_layer.bias.data
               layer.rho_bias.data = get_rho(det_layer.bias.data, delta)
        elif (str(layer) == 'LinearReparameterization()'
                or str(layer) == 'LinearFlipout()'):
            #set the priors
            layer.prior_weight_mu = det_layer.weight.data
            if layer.prior_bias_mu is not None:
               layer.prior_bias_mu.data = det_layer.bias

            #initialize the surrogate posteriors
            layer.mu_weight.data = det_layer.weight.data
            layer.rho_weight.data = get_rho(det_layer.weight.data, delta)
            if layer.mu_bias is not None:
               layer.mu_bias.data = det_layer.bias.data
               layer.rho_bias.data = get_rho(det_layer.bias.data, delta)

        elif str(layer).startswith('Batch'):
            #initialize parameters
            layer.weight.data = det_layer.weight.data
            if layer.bias is not None:
               layer.bias.data = det_layer.bias
            layer.running_mean.data = det_layer.running_mean.data
            layer.running_var.data = det_layer.running_var.data
            layer.num_batches_tracked.data = det_layer.num_batches_tracked.data

    model.state_dict()
    return model

In [ ]:
!pip install tqdm


In [ ]:
from tqdm import tqdm


# Define the number of samples for uncertainty estimation
num_samples = 10

# Initialize dictionaries to store uncertainties
uncertainties_original = []
uncertainties_generated = []

# Define the device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model5.to(device)
model5.eval()

# Assuming generator is defined and moved to the correct device
generator.to(device)

# Iterate over the test set
for inputs, labels in tqdm(test_loader, desc="Processing test set"):
    inputs, labels = inputs.to(device), labels.to(device)

    # Lists to store outputs for sampling
    all_outputs_original = []
    all_outputs_generated = []

    # Collect multiple samples for the original inputs
    for _ in range(num_samples):
        sample_outputs, _ = model5(inputs)
        all_outputs_original.append(sample_outputs)

    # Average the outputs
    outputs_original = torch.mean(torch.stack(all_outputs_original), dim=0)

    # Generate data using the generator
    generated_data = generator(torch.randn(4, 16, 12).to(device))
    for _ in range(num_samples):
        sample_outputs, _ = model5(generated_data)
        all_outputs_generated.append(sample_outputs)
    outputs_generated = torch.mean(torch.stack(all_outputs_generated), dim=0)

    # Calculate uncertainties
    uncertainty_original = predictive_entropy(outputs_original.data.cpu().numpy())
    uncertainty_generated = predictive_entropy(outputs_generated.data.cpu().numpy())

    # Append uncertainties to the lists
    uncertainties_original.append(uncertainty_original)
    uncertainties_generated.append(uncertainty_generated)

# Calculate mean uncertainties for original and generated data
mean_uncertainty_original = sum(uncertainties_original) / len(uncertainties_original)
mean_uncertainty_generated = sum(uncertainties_generated) / len(uncertainties_generated)

# Print mean uncertainties
print(f'Mean Predictive Uncertainty on Original Data: {mean_uncertainty_original:.4f}')
print(f'Mean Predictive Uncertainty on Generated Data: {mean_uncertainty_generated:.4f}')


In [ ]:
# Scatter plot without connecting the points
plt.figure(figsize=(10, 6))
plt.scatter(range(len(uncertainties_original)), uncertainties_original, label='Original Uncertainty', marker='o', color='b')
plt.scatter(range(len(uncertainties_generated)), uncertainties_generated, label='Generated Uncertainty', marker='x', color='r')

# Adding title and labels
plt.title("Comparison of Original and Generated data predictive_entropy")
plt.xlabel("Sample Index")
plt.ylabel("Uncertainty Value")
plt.legend()
plt.savefig("uncertainity_predictive_entropy.png",dpi=300)


# Show the plot
plt.grid(True)
plt.show()


In [ ]:
from tqdm import tqdm


# Define the number of samples for uncertainty estimation
num_samples = 10

# Initialize dictionaries to store uncertainties
uncertainties_original = []
uncertainties_generated = []

# Define the device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model5.to(device)
model5.eval()

# Assuming generator is defined and moved to the correct device
generator.to(device)

# Iterate over the test set
for inputs, labels in tqdm(test_loader, desc="Processing test set"):
    inputs, labels = inputs.to(device), labels.to(device)

    # Lists to store outputs for sampling
    all_outputs_original = []
    all_outputs_generated = []

    # Collect multiple samples for the original inputs
    for _ in range(num_samples):
        sample_outputs, _ = model5(inputs)
        all_outputs_original.append(sample_outputs)

    # Average the outputs
    outputs_original = torch.mean(torch.stack(all_outputs_original), dim=0)

    # Generate data using the generator
    generated_data = generator(torch.randn(4, 16, 12).to(device))
    for _ in range(num_samples):
        sample_outputs, _ = model5(generated_data)
        all_outputs_generated.append(sample_outputs)
    outputs_generated = torch.mean(torch.stack(all_outputs_generated), dim=0)

    # Calculate uncertainties
    uncertainty_original = mutual_information(outputs_original.data.cpu().numpy())
    uncertainty_generated = mutual_information(outputs_generated.data.cpu().numpy())

    # Append uncertainties to the lists
    uncertainties_original.append(uncertainty_original)
    uncertainties_generated.append(uncertainty_generated)

# Calculate mean uncertainties for original and generated data
mean_uncertainty_original = sum(uncertainties_original) / len(uncertainties_original)
mean_uncertainty_generated = sum(uncertainties_generated) / len(uncertainties_generated)

# Print mean uncertainties
print(f'Mean Predictive Uncertainty on Original Data: {mean_uncertainty_original:.4f}')
print(f'Mean Predictive Uncertainty on Generated Data: {mean_uncertainty_generated:.4f}')


In [ ]:
# Scatter plot without connecting the points
plt.figure(figsize=(10, 6))
plt.scatter(range(len(uncertainties_original)), uncertainties_original, label='Original Uncertainty', marker='o', color='b')
plt.scatter(range(len(uncertainties_generated)), uncertainties_generated, label='Generated Uncertainty', marker='x', color='r')

# Adding title and labels
plt.title("Comparison of Original and Generated data mutual_information")
plt.xlabel("Sample Index")
plt.ylabel("Uncertainty Value")
plt.legend()
plt.savefig("uncertainity_mutual_information.png",dpi=300)


# Show the plot
plt.grid(True)
plt.show()


In [ ]:
from tqdm import tqdm
from sklearn.cluster import KMeans
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix
import matplotlib.pyplot as plt

# Define the number of samples for uncertainty estimation
num_samples = 10

# Initialize lists to store uncertainties
uncertainties_original = []
uncertainties_generated = []

# Define the device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model5.to(device)
model5.eval()

# Assuming generator is defined and moved to the correct device
generator.to(device)


# Initialize lists to store uncertainties
uncertainties_original = []
uncertainties_generated = []

# Iterate over the test set to gather PE and MI
for inputs, labels in tqdm(test_loader, desc="Processing test set"):
    inputs, labels = inputs.to(device), labels.to(device)

    all_outputs_original = []
    all_outputs_generated = []

    # Collect multiple samples for the original inputs
    for _ in range(num_samples):
        sample_outputs, _ = model5(inputs)
        all_outputs_original.append(sample_outputs)

    outputs_original = torch.mean(torch.stack(all_outputs_original), dim=0)

    # Generate data using the generator
    generated_data = generator(torch.randn(4, 16, 12).to(device))
    for _ in range(num_samples):
        sample_outputs, _ = model5(generated_data)
        all_outputs_generated.append(sample_outputs)
    outputs_generated = torch.mean(torch.stack(all_outputs_generated), dim=0)

    # Calculate uncertainties
    uncertainty_original_pe = predictive_entropy(outputs_original.data.cpu().numpy())
    uncertainty_generated_pe = predictive_entropy(outputs_generated.data.cpu().numpy())
    
    uncertainty_original_mi = mutual_information(outputs_original.data.cpu().numpy())
    uncertainty_generated_mi = mutual_information(outputs_generated.data.cpu().numpy())

    uncertainties_original.append((uncertainty_original_pe, uncertainty_original_mi))
    uncertainties_generated.append((uncertainty_generated_pe, uncertainty_generated_mi))

# Convert lists to NumPy arrays
uncertainties_original = np.array(uncertainties_original)
uncertainties_generated = np.array(uncertainties_generated)

# Calculate JEM for original and generated data
def calculate_jem(uncertainties, lambda_weight):
    return  uncertainties[:, 0] + uncertainties[:, 1]

jem_original = calculate_jem(uncertainties_original, lambda_weight)
jem_generated = calculate_jem(uncertainties_generated, lambda_weight)

# Combine JEM values for clustering
all_jem_values = np.concatenate([jem_original, jem_generated])

# Apply KMeans clustering
num_clusters = 2
kmeans = KMeans(n_clusters=num_clusters, random_state=0)
clusters = kmeans.fit_predict(all_jem_values.reshape(-1, 1))

# Calculate means of clusters
cluster_means = [all_jem_values[clusters == i].mean() for i in range(num_clusters)]

# Assign labels based on cluster means
assigned_labels = np.zeros_like(clusters)
if cluster_means[0] > cluster_means[1]:
    assigned_labels[clusters == 0] = 0
    assigned_labels[clusters == 1] = 1
else:
    assigned_labels[clusters == 0] = 1
    assigned_labels[clusters == 1] = 0

# Combine true labels for evaluation
true_labels_original = np.zeros(len(jem_original))  # Original data
true_labels_generated = np.ones(len(jem_generated))  # Generated data
all_true_labels = np.concatenate([true_labels_original, true_labels_generated])

# Calculate accuracies
accuracy_original = accuracy_score(true_labels_original, assigned_labels[:len(jem_original)])
accuracy_generated = accuracy_score(true_labels_generated, assigned_labels[len(jem_original):])

# Print accuracies
print(f'Accuracy for Original Data: {accuracy_original:.4f}')
print(f'Accuracy for Generated Data: {accuracy_generated:.4f}')

# Overall metrics
overall_accuracy = accuracy_score(all_true_labels, assigned_labels)
overall_precision = precision_score(all_true_labels, assigned_labels)
overall_recall = recall_score(all_true_labels, assigned_labels)
overall_f1 = f1_score(all_true_labels, assigned_labels)

# Print overall metrics
print(f'Overall Accuracy: {overall_accuracy:.4f}')
print(f'Overall Precision: {overall_precision:.4f}')
print(f'Overall Recall: {overall_recall:.4f}')
print(f'Overall F1-Score: {overall_f1:.4f}')

# Plot the results
plt.figure(figsize=(8, 5))
plt.bar(['Original Data', 'Generated Data'], [accuracy_original, accuracy_generated], color=['blue', 'orange'])
plt.ylabel('Accuracy')
plt.title('Classification Accuracy for Original vs Generated Data')
plt.show()


In [ ]:
# Scatter plot without connecting the points
plt.figure(figsize=(10, 6))

# Plot original uncertainty values with cluster colors
plt.scatter(range(len(jem_original)), 
            jem_original, 
            label='Original data JEM', 
            marker='o', 
            color=['blue' if cluster == 0 else 'orange' for cluster in clusters[:len(jem_original)]])

# Plot generated uncertainty values with cluster colors
plt.scatter(range(len(jem_generated)), 
            jem_generated, 
            label='Generated data JEM', 
            marker='x', 
            color=['blue' if cluster == 0 else 'orange' for cluster in clusters[len(jem_original):]])

# Adding title and labels
plt.title("Clustring of JEM values to Original and Generated Data by GAN-GRID")
plt.xlabel("Sample Index")
plt.ylabel("JEM Value")
plt.legend()
# Save the plot
plt.savefig("uncertainty_JEM.png", dpi=300)


# Show the plot
plt.grid(True)
plt.show()


In [ ]:
print(cluster_means[0])
print(cluster_means[1])